# Initial data processing

## Cleaning the data

We are using human-generated neural reconstructions as our ground truth. The first step is to get rid of comments in the header of the file

In [64]:
import os

def get_human_trajectories():
    file_list = glob.glob("../data/human/*.swc")
    return file_list

def remove_comments(fpaths, fnames):
    """SWC files start with comments, remove before proceeding"""
    for i in range(len(fpaths)):

        input = open(fpaths[i], "r")
        outdir = "../data/human_clean/"
        outdir = os.path.abspath(outdir)
        if not os.path.exists(outdir):
            os.mkdir(outdir)
        outfile = os.path.join(outdir, fnames[i])
        output = open(outfile, "w+")

        for line in input:
            if not line.lstrip().startswith("#"):
                output.write(line)

        input.close()
        output.close()

def main():
    # get human trajectories
    fnames = []
    abs_paths = []
    for root, dirs, fnames_ in os.walk("../data/human/"):
        fnames.extend(fnames_)
        for f in fnames_:
            relpath = os.path.join(root, f)
            abs_path = os.path.abspath(relpath)
            abs_paths.append(abs_path)

    remove_comments(abs_paths, fnames)


main()

Next, we need to split each file into its component branches. The SWC files have the following columns:

`node_id type x_coordinate y_coordinate z_coordinate radius parent_node`

First, I convert the SWC file into a linked list.

In [75]:
from collections import defaultdict

def file_to_linked_list(fpath: list):
    
    # https://stackoverflow.com/a/17756005/4212158
    linked_list = defaultdict(list)
    
    input = open(fpath, "r")
    for line in input:
        # note: if the parent node is -1, then the child_node_id is the true identity of the root node
        child_node_id, type_, x_coord, y_coord, z_coord, radius, parent_node = line.split()
        new_node = (child_node_id, x_coord, y_coord, z_coord)
        if (len(new_node) != 4 and isinstance(new_node, tuple)):
            raise Exception("faulty node: {}".format(new_node))
        linked_list[parent_node].append(new_node)
    
    input.close()
    return linked_list


## Chopping  reconstructions into individual branches

I start tracing the neuron starting at each root node, which by convention has a parent_node_id of -1. From each root node, I start to grow the branch

In [76]:
def chop_graph(fname: str, linked_list: dict):
    """take a single reconstruction, and chop it up at every fork"""
    assert isinstance(linked_list, dict)
    
    root_nodes = linked_list["-1"]
    for i, root_node in enumerate(root_nodes):
        #print("scanning {} root node {} of {}".format(fname, i, len(root_nodes)))
        root_node_id, _x_coord, _y_coord, _z_coord = root_node
        assert(len(root_node) == 4  and isinstance(root_node, tuple))
        #print("root node ", root_node)

        child_nodes = linked_list[root_node_id]
        for j, child_node in enumerate(child_nodes):
            #print("starting child {} of {}".format(j, len(child_nodes)))
            #print("child node ", child_node)
            child_node_id,  _x_coord, _y_coord, _z_coord = child_node
            assert(len(child_node) == 4  and isinstance(child_node, tuple))
            branch_name = "_".join([fname, "root{}".format(root_node_id), "child{}".format(child_node_id)])
            grow_branch(linked_list, root_node, child_node, branch_name)
            
            

I grow each branch until I encounter a fork. Forks are easy to find because the parent node will have more than one child. When the 

In [80]:
def grow_branch(linked_list: dict, root_node: tuple, first_child_node: tuple, branch_name: str):
    """grow the branch until there's a fork"""
    assert isinstance(linked_list, dict)
    assert isinstance(root_node, tuple)
    assert isinstance(first_child_node, tuple)
    
    # initialize the branch
    #print("new branch started: {}".format(branch_name))
    branch = [root_node, first_child_node]
    
    end_found = False
    parent_node = first_child_node
    while not end_found:
        if (len(branch) % 1500 == 0):
            print("{} nodes processed".format(len(branch)))
        
        # num nodes in a branch should never be > #nodes in whole tree
        if (len(branch) > len(linked_list)):
            print(branch)
            raise Exception("this is growing out of control")
        try:
            parent_node_id = parent_node[0]
            child_nodes = linked_list[parent_node_id]
            assert(isinstance(child_nodes, list))
            if len(child_nodes) > 1: # fork found, chop some more
                print("fork found after {} nodes".format(len(branch)))
                save_branch_as_swc(branch, branch_name)
                for i, child_node in enumerate(child_nodes):
                    child_node_id = child_node[0]
                    child_branch_name = "_".join(branch_name, "grandchild{}".format(child_node_id))
                    grow_branch(linked_list, parent_node, child_node)
                end_found = True
            elif len(child_nodes) == 0:  # no more children, end of branch
                print("end of branch {} found after {} nodes".format(branch_name, len(branch)))
                save_branch_as_swc(branch, branch_name)
                end_found = True
            else:  # no branch, so only one child node
                assert (len(child_nodes) == 1)
                child_node = child_nodes[0]  # should be list w single tuple
                branch.append(child_node)  # should be just 1 node
                child_node_id = child_node[0]  # unpack node from list first
                assert child_node != parent_node
                parent_node = child_node  # start new round
        except:
            raise
                

Finally, save each branch as its own SWC file. Reminder, the column order convention is 

`node_id type x_coordinate y_coordinate z_coordinate radius parent_node`

In [81]:
def save_branch_as_swc(branch: list, branch_name: str):
    assert(isinstance(branch, list))
    outdir = "../data/human_splitted/"
    outdir = os.path.abspath(outdir)
    if not os.path.exists(outdir):
        os.mkdir(outdir)
    outfile = os.path.join(outdir, branch_name+".swc")
    #print("saving SWC {}".format(branch_name))
    output = open(outfile, "w+")
    
    default_radius = "1.0"
    default_type = "3"
    
    parent_node_id = "-1"
    for i, node in enumerate(branch):
        try:
            child_node_id, x, y, z = node
        except ValueError:
            print("error in save-branch", len(node), node)
            raise
        # this is the SWC file convention
        swc_items = [child_node_id, default_type, x, y, z, default_radius, parent_node_id]
        #swc_items = [str(item) for item in str_items]
        try:
            swc_line = " ".join(swc_items)
        except:
            print(swc_items)
            for item in swc_items:
                print(type(item))
                raise
        output.write(swc_line)
        parent_node_id = child_node_id

    output.close()

Now, we can go through the list of clean files and actually split everything.

In [83]:
clean_files = []
fnames = []
for root, dirs, fnames_ in os.walk("../data/human_clean/"):
        fnames.extend(fnames_)
        for f in fnames_:
            relpath = os.path.join(root, f)
            abs_path = os.path.abspath(relpath)
            clean_files.append(abs_path)
assert len(clean_files) == len(fnames), "# file paths and fnames don't match: {} and {}".format(len(clean_files), len(fnames))

#linked_lists = []
for i in range(len(fnames)):
    #print("#{} parsing {} to linked list".format(i, fnames[i]))
    linked_list = file_to_linked_list(clean_files[i])
    print("#{} splitting {} to branches".format(i, fnames[i]))
    chop_graph(fnames[i], linked_list)

#0 splitting 110_ZWX_LijLiu_06072018.ano.swc to branches
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5497882_child5497881 found after 6 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5501825_child5501824 found after 13 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5498858_child5498857 found after 48 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5496748_child5496747 found after 56 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5502730_child5502729 found after 31 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5496692_child5496691 found after 47 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5496804_child5496803 found after 56 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5496937_child5496936 found after 54 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5504420_child5504419 found after 29 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5487621_child5487620 found after 60 nodes
end of branch 110_ZWX_Li

end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5502699_child5502698 found after 25 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5504932_child5504931 found after 24 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5493669_child5493668 found after 67 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5498198_child5498197 found after 64 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5486233_child5486232 found after 14 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5505561_child5505560 found after 50 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5487045_child5487044 found after 21 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5497506_child5497505 found after 13 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5489179_child5489178 found after 24 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5500550_child5500549 found after 19 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5491568_child5491567 found aft

end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5491201_child5491200 found after 54 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5490042_child5490041 found after 9 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5499113_child5499112 found after 15 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5495460_child5495459 found after 8 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5496275_child5496274 found after 27 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5490033_child5490032 found after 27 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5500436_child5500435 found after 35 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5505388_child5505387 found after 11 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5500102_child5500101 found after 11 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5492182_child5492181 found after 7 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5502674_child5502673 found after 

end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5490846_child5490845 found after 10 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5501150_child5501149 found after 16 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5505594_child5505593 found after 17 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5500999_child5500998 found after 6 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5488321_child5488320 found after 7 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5486760_child5486759 found after 26 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5498944_child5498943 found after 6 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5491515_child5491514 found after 28 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5491524_child5491523 found after 9 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5493085_child5493084 found after 12 nodes
end of branch 110_ZWX_LijLiu_06072018.ano.swc_root5495037_child5495036 found after 2

end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2213557_child2213556 found after 5 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2213575_child2213574 found after 18 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2213552_child2213551 found after 20 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2209330_child2209329 found after 22 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2209418_child2209417 found after 12 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2209270_child2209269 found after 12 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2215412_child2215411 found after 14 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2215478_child2215477 found after 16 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2212639_child2212638 found after 36 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2215398_child2215397 found after 16 nodes
end of branch 103_ZSJ_LijLiu_06072018.ano.swc_root2211946_child2211945 found afte

...

#52 splitting 083_LiuAn_LijLiu_06052018.ano.swc to branches
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257171_child2257170 found after 27 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257047_child2257046 found after 26 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257137_child2257136 found after 68 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257069_child2257068 found after 22 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257193_child2257192 found after 2 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257191_child2257190 found after 20 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257144_child2257143 found after 7 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2257281_child2257280 found after 88 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2248347_child2248346 found after 26 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2248312_child2248311 found after 22 nodes
en

end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2439456_child2439455 found after 23 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2439324_child2439323 found after 9 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2439132_child2439131 found after 8 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2440688_child2440687 found after 13 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2443303_child2443302 found after 18 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2439378_child2439377 found after 21 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2443093_child2443092 found after 31 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2439484_child2439483 found after 22 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2439124_child2439123 found after 7 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2443482_child2443481 found after 12 nodes
end of branch 083_LiuAn_LijLiu_06052018.ano.swc_root2443870_chi

end of branch 037_06082018.ano.swc_root21854_child21853 found after 56 nodes
end of branch 037_06082018.ano.swc_root21344_child21343 found after 24 nodes
end of branch 037_06082018.ano.swc_root21388_child21387 found after 44 nodes
end of branch 037_06082018.ano.swc_root21424_child21423 found after 36 nodes
end of branch 037_06082018.ano.swc_root21474_child21473 found after 5 nodes
end of branch 037_06082018.ano.swc_root21469_child21468 found after 11 nodes
end of branch 037_06082018.ano.swc_root1188231_child1188230 found after 34 nodes
end of branch 037_06082018.ano.swc_root21487_child21486 found after 6 nodes
end of branch 037_06082018.ano.swc_root1188268_child1188267 found after 13 nodes
end of branch 037_06082018.ano.swc_root1188255_child1188254 found after 5 nodes
end of branch 037_06082018.ano.swc_root1188248_child1188247 found after 7 nodes
end of branch 037_06082018.ano.swc_root1188250_child1188249 found after 2 nodes
end of branch 037_06082018.ano.swc_root21511_child21510 found

end of branch 037_06082018.ano.swc_root1174212_child1174211 found after 10 nodes
end of branch 037_06082018.ano.swc_root1191044_child1191043 found after 8 nodes
end of branch 037_06082018.ano.swc_root1174766_child1174765 found after 27 nodes
end of branch 037_06082018.ano.swc_root1174605_child1174604 found after 9 nodes
end of branch 037_06082018.ano.swc_root1175985_child1175984 found after 5 nodes
end of branch 037_06082018.ano.swc_root1183862_child1183861 found after 9 nodes
end of branch 037_06082018.ano.swc_root1184856_child1184855 found after 12 nodes
end of branch 037_06082018.ano.swc_root1178834_child1178833 found after 11 nodes
end of branch 037_06082018.ano.swc_root1184345_child1184344 found after 7 nodes
end of branch 037_06082018.ano.swc_root1180263_child1180262 found after 9 nodes
end of branch 037_06082018.ano.swc_root1174375_child1174374 found after 10 nodes
end of branch 037_06082018.ano.swc_root1174716_child1174715 found after 2 nodes
end of branch 037_06082018.ano.swc_

end of branch 037_06082018.ano.swc_root1191079_child1191078 found after 15 nodes
end of branch 037_06082018.ano.swc_root1185228_child1185227 found after 25 nodes
end of branch 037_06082018.ano.swc_root1174040_child1174039 found after 26 nodes
end of branch 037_06082018.ano.swc_root1180357_child1180356 found after 10 nodes
end of branch 037_06082018.ano.swc_root1180398_child1180397 found after 9 nodes
end of branch 037_06082018.ano.swc_root1178613_child1178612 found after 8 nodes
end of branch 037_06082018.ano.swc_root1180389_child1180388 found after 10 nodes
end of branch 037_06082018.ano.swc_root1188980_child1188979 found after 2 nodes
end of branch 037_06082018.ano.swc_root1180058_child1180057 found after 17 nodes
end of branch 037_06082018.ano.swc_root1183065_child1183064 found after 18 nodes
end of branch 037_06082018.ano.swc_root1191393_child1191392 found after 27 nodes
end of branch 037_06082018.ano.swc_root1186651_child1186650 found after 22 nodes
end of branch 037_06082018.ano.